# Project Phase 3: Video Moment Detection

## Connection to Opensearch index

In [1]:
import pprint as pp
import requests

host = 'localhost'
port = 9200

user = 'admin' # Add your user name here.
password = 'a.Zerty12.3' # Add your user password here. For testing only. Don't store credentials in code. 
index_name = user

In [2]:
import pprint as pp
from opensearchpy import OpenSearch
from opensearchpy import helpers

# Create the client with SSL/TLS enabled, but hostname verification disabled.
client = OpenSearch(
    hosts = [{'host': host, 'port': port}],
    http_auth = (user, password),
    use_ssl = True,
    verify_certs = False,
)

if client.indices.exists(index_name):

    resp = client.indices.open(index = index_name)
    print(resp)

    print('\n----------------------------------------------------------------------------------- INDEX SETTINGS')
    settings = client.indices.get_settings(index = index_name)
    pp.pprint(settings)

    print('\n----------------------------------------------------------------------------------- INDEX MAPPINGS')
    mappings = client.indices.get_mapping(index = index_name)
    pp.pprint(mappings)

    print('\n----------------------------------------------------------------------------------- INDEX #DOCs')
    print(client.count(index = index_name))
else:
    print("Index does not exist.")

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/opensearchpy/connection/http_urllib3.py:214: UserWarning: Connecting to https://localhost:9200 using SSL with verify_certs=False is insecure.
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made 

{'acknowledged': True, 'shards_acknowledged': True}

----------------------------------------------------------------------------------- INDEX SETTINGS
{'admin': {'settings': {'index': {'creation_date': '1744390732761',
                                  'knn': 'true',
                                  'number_of_replicas': '0',
                                  'number_of_shards': '4',
                                  'provided_name': 'admin',
                                  'refresh_interval': '-1',
                                  'replication': {'type': 'DOCUMENT'},
                                  'uuid': 'xP6gIjL3Sxat9ExXWgFfCg',
                                  'version': {'created': '136347827'}}}}}

----------------------------------------------------------------------------------- INDEX MAPPINGS
{'admin': {'mappings': {'properties': {'caption_bow': {'analyzer': 'standard',
                                                       'type': 'text'},
                           

## Video downloading

In [3]:
import os
import subprocess

# Directory where videos will be saved
download_path = "./videos_part3"
os.makedirs(download_path, exist_ok=True)  # Create folder if it doesn't exist

video_url = "https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c" # Replace with the actual video URL
video_id = video_url.split("=")[1]  # Extracted video ID from the URL
#print(f"Video ID: {video_id}")

# Loop through each video in the top 10
output_template = os.path.join(download_path, f"{video_id}.mp4")

try:
    print(f"Downloading: {video_url}")
    subprocess.run(["yt-dlp", "-o", output_template, video_url], check=True)
    print(f"Downloaded: {output_template}")
except subprocess.CalledProcessError:
    print(f"Failed to download {video_id}.")

Downloading: https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c
[youtube] Extracting URL: https://youtu.be/daxodF_Pnzg?si=GM0lJFcjXopRpQ2c
[youtube] daxodF_Pnzg: Downloading webpage
[youtube] daxodF_Pnzg: Downloading tv client config
[youtube] daxodF_Pnzg: Downloading tv player API JSON
[youtube] daxodF_Pnzg: Downloading ios player API JSON
[youtube] daxodF_Pnzg: Downloading m3u8 information
[info] daxodF_Pnzg: Downloading 1 format(s): 18
[download] ./videos_part3/GM0lJFcjXopRpQ2c.mp4 has already been downloaded
[download] 100% of    9.44MiB
Downloaded: ./videos_part3/GM0lJFcjXopRpQ2c.mp4


## Frames extraction

In [4]:
import av
import av.datasets
import os

output_folder = "./frames_part3"
input_folder = "./videos_part3"
video = "/GM0lJFcjXopRpQ2c.mp4"
# File name without extension
filename = os.path.splitext(video)[0]
if not os.path.isdir(output_folder + "/" + filename):
    os.makedirs(output_folder + "/" + filename)
with av.open(input_folder + video) as container:
    stream = container.streams.video[0]
    # We want 2 frame per second
    fps = stream.average_rate
    interval = int(round(fps*0.5))
    #print(fps)
    cpt = 0
    for i,frame in enumerate(container.decode(stream)):
        if i % interval == 0:
            frame.to_image().save(output_folder+"/"+filename+"/"+str(cpt*(0.5))+".jpg", quality=80)
            cpt += 1

## Opensearch index update

In [5]:
# Give every documents added to the index: just to check how the index looks like
client.indices.refresh(index=index_name)
query = {
    "query": {
        "match_all": {}
    },
    "size": 100  # Adjust the number to see more results if needed
}

response = client.search(
    index=index_name,
    body=query
)

# Print the total number of documents and some of the documents
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])  # Print the source of each document

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Total hits: 4822
{'video_id': 'oGwn4NUeoy8', 'moment_description': 'A small group of people are seen on a stage getting their instruments ready.', 'frame_path': './frames/oGwn4NUeoy8/7.jpg', 'caption_bow': ['seen', 'are', 'small', 'their', 'of', 'a', 'getting', 'ready.', 'group', 'stage', 'instruments', 'on', 'people'], 'caption_vec': [0.039015624672174454, -0.017577411606907845, -0.020665453746914864, -0.04817619547247887, -0.11232907325029373, 0.037931185215711594, 0.012609592638909817, 0.011078917421400547, 0.013040421530604362, 0.017808284610509872, 0.011674837209284306, -0.05383112281560898, -0.005015570204705, -0.048096999526023865, -0.007173283491283655, -0.04769686236977577, 0.06541087478399277, -0.07373795658349991, -0.04303865134716034, -0.02477027289569378, -0.09667882323265076, -0.0012850348139181733, -0.07670816779136658, 0.012383149936795235, -0.007747381925582886, 0.0011938927927985787, -0.103289395570755, -0.001279788906686008, 0.09031550586223602, -0.012941332533955574

In [6]:
import os

frames_directory = "./frames_part3/" 

# For each frame in the directory, create a document and add it to the index
for subfolder in os.listdir(frames_directory):
    subfolder_path = os.path.join(frames_directory, subfolder)

    # Check if the subfolder is indeed a directory
    if os.path.isdir(subfolder_path):
        video_id = subfolder
        print(video_id + " subfolder found.")

        # Iterate through each frame in the subfolder
        for frame in os.listdir(frames_directory + subfolder):
            frame_path = os.path.join(frames_directory + subfolder, frame)
            print(frame_path)
            
            # Check the file extension to ensure it's an image
            if frame.lower().endswith(('.png', '.jpg', '.jpeg')):
                document = {
                    "video_id": video_id,
                    "moment_description": None,
                    "frame_path": frame_path,
                    "caption_bow": None,
                    "caption_vec": None,
                    "visual_description_vec": None,
                    "frame_vec": None,
                    "end_timestamp": None,
                    "start_timestamp": None,
                    "video_length": None,
                }

                # Add the document to the index
                response = client.index(
                    index=index_name,
                    body=document
                )
                #print(f"Document added for frame: '{frame}':", response)


GM0lJFcjXopRpQ2c subfolder found.
./frames_part3/GM0lJFcjXopRpQ2c/97.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/150.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/7.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/172.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/140.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/141.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/139.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/92.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/183.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/61.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/155.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/188.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/118.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/77.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/187.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/174.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/169.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/153.0.jpg


/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/sit

./frames_part3/GM0lJFcjXopRpQ2c/152.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/50.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/128.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/25.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/54.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/47.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/194.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/204.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/1.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/63.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/167.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/26.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/100.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/201.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/87.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/41.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/32.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/12.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/197.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/53.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/84.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/132.5.jpg


/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/sit

./frames_part3/GM0lJFcjXopRpQ2c/72.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/131.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/148.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/203.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/56.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/136.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/193.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/69.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/29.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/36.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/93.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/99.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/111.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/91.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/115.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/204.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/186.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/78.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/90.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/12.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/133.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/39.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/71.0.jpg


...

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/sit

./frames_part3/GM0lJFcjXopRpQ2c/95.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/13.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/101.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/161.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/102.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/82.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/129.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/22.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/85.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/17.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/135.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/92.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/183.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/10.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/129.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/48.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/114.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/181.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/115.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/52.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/80.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/117.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/185.0.jpg


/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/sit

./frames_part3/GM0lJFcjXopRpQ2c/9.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/58.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/124.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/66.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/168.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/55.5.jpg
./frames_part3/GM0lJFcjXopRpQ2c/178.0.jpg
./frames_part3/GM0lJFcjXopRpQ2c/27.5.jpg


/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/sit

In [7]:
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

Total hits: 2514
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/92.0.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': [0.012399778701364994, 0.01585768535733223, 0.02183917723596096, 0.009679186157882214, -0.04274068400263786, -0.029000133275985718, 0.02698618546128273, 0.036603894084692, 0.006510015577077866, -0.02537582442164421, 0.004612692631781101, -0.005632247310131788, 0.05218495428562164, 0.04607249051332474, -0.03585195541381836, 0.028584787622094154, -0.0858360156416893, 0.008683317340910435, 0.047516025602817535, -0.02166920155286789, -0.0654725506901741, -0.0005360718932934105, 0.018567070364952087, 0.029224881902337074, 0.012090884149074554, 0.016963500529527664, -0.011695170775055885, 0.03870437666773796, -0.003500860184431076, 0.008343765512108803, 0.00554330088198185, -0.011082974262535572, -0.02231128141283989, 0.00977570191025734, -0.020671330392360687, 0.007708761

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


## Captions generations

In [8]:
from ollama import Client

client_llava = Client(
  host='https://twiz.novasearch.org/ollama',
  headers={'x-some-header': 'some-value'}
)

client_os = client

model_multimodal = 'llava-phi3:latest'

In [9]:
from transformers import CLIPModel, CLIPProcessor

# Load the clip Model and Processor
model_name = "openai/clip-vit-base-patch32"
model = CLIPModel.from_pretrained(model_name)
processor = CLIPProcessor.from_pretrained(model_name)

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.


In [ ]:
import torch

def encode_text(caption):

    inputs = processor(text=caption, return_tensors="pt", padding=True, truncation=True, max_length=77)

    # Encode the caption to get the embedding
    with torch.no_grad():
        embedding = model.get_text_features(**inputs)
    
    # Normalize the caption embedding
    embedding = embedding / embedding.norm(dim=-1, keepdim=True)

    return embedding.numpy()[0]

In [11]:
# Function to generate descriptions for frames without moment_description
def generate_missing_descriptions():
    """
    1. Retrieve all frames without descriptions
    2. Use LLaVA to generate descriptions
    3. Update OpenSearch with the descriptions and their embeddings
    """

    # Retrieve all documents without descriptions
    client_os.indices.refresh(index=index_name)
    query = {
        "query": {
            "bool": {
                "must_not": {
                    "exists": {
                        "field": "moment_description"
                    }
                }
            }
        },
        "size": 3000
    }

    response = client_os.search(
        index=index_name,
        body=query
    )

    total_documents = len(response['hits']['hits'])
    print(f"Found {total_documents} frames without descriptions")

    # Process each frame to generate a description
    for i, doc in enumerate(response['hits']['hits']):
        doc_id = doc['_id']
        frame_path = doc['_source']['frame_path']

        print(f"Processing frame {i + 1}/{total_documents}: {frame_path}")

        # Use LLaVA to generate a description
        llava_response = client_llava.chat(
            model=model_multimodal,
            messages=[
                {
                    'role': 'user',
                    'content': 'Describe this image frame from a video in one concise sentence.',
                    'images': [frame_path]
                },
            ]
        )

        # Extract the generated description
        generated_description = llava_response.message.content.strip()

        # Generate CLIP embedding for the description
        description_embedding = encode_text(generated_description)

        # Update the document in OpenSearch
        update_body = {
            "doc": {
                "moment_description": generated_description,
                "visual_description_vec": description_embedding.tolist()
            }
        }

        update_response = client_os.update(
            index=index_name,
            id=doc_id,
            body=update_body
        )

        if i % 10 == 0:  # Log progress every 10 frames
            print(f"Progress: {i + 1}/{total_documents}")

    print("Description generation complete!")
    return total_documents

In [12]:
# Execute the function to generate missing descriptions
num_updated = generate_missing_descriptions()
print(f"Generated descriptions for {num_updated} frames")

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Found 2514 frames without descriptions
Processing frame 1/2514: ./frames_part3/GM0lJFcjXopRpQ2c/140.5.jpg


NameError: name 'torch' is not defined

## Captions encoding

### Frame embedding and index update (if needed)

In [ ]:
import torch
import numpy as np
from PIL import Image
from transformers import CLIPProcessor, CLIPModel

# Load the clip Model and Processor
model_name = "openai/clip-vit-base-patch32"
model = CLIPModel.from_pretrained(model_name)
processor = CLIPProcessor.from_pretrained(model_name)

# Encoding function
def encode_image(image_path):
    image = Image.open(image_path).convert("RGB") # Ensure the image is in RGB format

    # Prepare the image for the model
    inputs = processor(images=image, return_tensors="pt", truncation=True, max_length=77)

    # Encode the image to get the embedding
    with torch.no_grad():
        image_features = model.get_image_features(**inputs)
    
    # Normalize the image embedding
    image_features = image_features / image_features.norm(p=2, dim=-1, keepdim=True)

    return image_features.numpy()[0]


# Iterate on the documents
query = {
    "query": {
            "bool": {
                "must_not": {
                    "exists": {
                        "field": "moment_description"
                    }
                }
            }
        },
}

# Retrieve all documents from the index
response = client.search(index=index_name, body=query, size=3000)
documents = response["hits"]["hits"]
# Add the embedding to each document
for doc in documents:
    doc_id = doc["_id"]  # ID document

    image_path = doc["_source"]["frame_path"]  # Get the image path from the document
    #print(image_path)
    embedding = encode_image(image_path)  # Get the embedding for the image

    # Update the document with the new field
    update_body = {
        "doc": {
            "frame_vec": embedding
        }
    }
    update_response = client.update(index=index_name, id=doc_id, body=update_body)

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
Using a slow image processor as `use_fast` is unset and a slow processor was saved with this model. `use_fast=True` will be the default behavior in v4.52, even if the model was saved with a slow processor. This will result in minor differences in outputs. You'll still be able to use a slow processor with `use_fast=False`.
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequ

In [ ]:
# Check the embeddings were added correctly
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


Total hits: 1676
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/140.5.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': [0.0070750233717262745, 0.004523462150245905, 0.022715900093317032, 0.009497295133769512, -0.0038220675196498632, -0.006738787516951561, 0.02429233491420746, 0.017196256667375565, 0.027631469070911407, -0.042262375354766846, -0.018703380599617958, -0.021906301379203796, 0.06799064576625824, 0.050219129770994186, -0.0369744598865509, 0.044161248952150345, -0.08401849865913391, 0.006614313926547766, 0.04619941487908363, -0.05016443878412247, -0.09714372456073761, -0.0028584590181708336, 0.019326884299516678, 0.04739337041974068, -0.004354060627520084, 0.02428525499999523, 0.008613518439233303, 0.02985638566315174, 0.011761745437979698, 0.018069369718432426, 0.001679958077147603, -0.00574698718264699, -0.005831253249198198, 0.023572426289319992, 0.00397148123010993, -0

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


### Caption embedding

In [ ]:
import torch
import numpy as np
from PIL import Image
from transformers import CLIPProcessor, CLIPModel

# Load the clip Model and Processor
model_name = "openai/clip-vit-base-patch32"
model = CLIPModel.from_pretrained(model_name)
processor = CLIPProcessor.from_pretrained(model_name)

# Encoding function
def encode_text(caption):

    inputs = processor(text=caption, return_tensors="pt", padding=True, truncation=True, max_length=77)

    # Encode the caption to get the embedding
    with torch.no_grad():
        embedding = model.get_text_features(**inputs)
    
    # Normalize the caption embedding
    embedding = embedding / embedding.norm(dim=-1, keepdim=True)

    return embedding.numpy()[0]


# Iterate on the documents
query = {
    "query": {
            "bool": {
                "must_not": {
                    "exists": {
                        "field": "visual_description_vec"
                    }
                }
            }
        },
}
# Retrieve all documents from the index
response = client.search(index=index_name, body=query, size=2000)
documents = response["hits"]["hits"]
# Add the embedding of the description to each document that have one
for doc in documents:
    doc_id = doc["_id"]  # ID document

    caption = doc["_source"]["moment_description"]  # Get the caption from the document
    
    if not caption == None:
        embedding = encode_text(caption)  # Get the embedding for the caption

        # Update the document with the new field
        update_body = {
            "doc": {
                "visual_description_vec": embedding
            }
        }
        update_response = client.update(index=index_name, id=doc_id, body=update_body)

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


In [ ]:
# Check the embeddings were added correctly
# Refresh the index to make sure all documents are searchable
client.indices.refresh(index=index_name)

# Retrieving and displaying the documents from the index to check if they were added correctly
query = {
    "query": {
        "match": {
            "video_id": "GM0lJFcjXopRpQ2c"
        }
    },
    "size": 100
}

response = client.search(
    index=index_name,
    body=query
)

# Print results
print(f"Total hits: {response['hits']['total']['value']}")
for hit in response['hits']['hits']:
    print(hit['_source'])

Total hits: 1676
{'video_id': 'GM0lJFcjXopRpQ2c', 'moment_description': None, 'frame_path': './frames_part3/GM0lJFcjXopRpQ2c/140.5.jpg', 'caption_bow': None, 'caption_vec': None, 'visual_description_vec': None, 'frame_vec': [0.0070750233717262745, 0.004523462150245905, 0.022715900093317032, 0.009497295133769512, -0.0038220675196498632, -0.006738787516951561, 0.02429233491420746, 0.017196256667375565, 0.027631469070911407, -0.042262375354766846, -0.018703380599617958, -0.021906301379203796, 0.06799064576625824, 0.050219129770994186, -0.0369744598865509, 0.044161248952150345, -0.08401849865913391, 0.006614313926547766, 0.04619941487908363, -0.05016443878412247, -0.09714372456073761, -0.0028584590181708336, 0.019326884299516678, 0.04739337041974068, -0.004354060627520084, 0.02428525499999523, 0.008613518439233303, 0.02985638566315174, 0.011761745437979698, 0.018069369718432426, 0.001679958077147603, -0.00574698718264699, -0.005831253249198198, 0.023572426289319992, 0.00397148123010993, -0

/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/home/hugo/NOVA/mpdw/env/lib/python3.12/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'localhost'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


## Regroupment based on clustering

## Frames fusionning